# A3: A\*, IDS, and Effective Branching Factor

For this assignment, implement the Recursive Best-First Search
implementation of the A\* algorithm given in class.  Name this function `aStarSearch`.  Also in this notebook include your `iterativeDeepeningSearch` functions.  Define a new function named `ebf` that returns an estimate of the effective
branching factor for a search algorithm applied to a search problem.

So, the required functions are

   - `aStarSearch(startState, actionsF, takeActionF, goalTestF, hF)`
   - `iterativeDeepeningSearch(startState, goalState, actionsF, takeActionF, maxDepth)`
   - `ebf(nNodes, depth)`, returns number of nodes expanded and depth reached during a search.

Apply `iterativeDeepeningSearch` and `aStarSearch` to several eight-tile sliding puzzle
problems. Compare their results by displayng
solution path depth, number of nodes 
generated, and the effective branching factor, and discuss the results.  Do this by defining the following function that prints the table as shown in the example below.

   - 'runExperiment(goalState1, goalState2, goalState3, [h1, h2, h3])

## Heuristic Functions

For `aStarSearch` use the following two heuristic functions, plus one more of your own design, for a total of three heuristic functions.

  * `h1(state, goal)`: $h(state, goal) = 0$, for all states $state$ and all goal states $goal$,
  * `h2(state, goal)`: $h(state, goal) = m$, where $m$ is the Manhattan distance that the blank is from its goal position,
  * `h3(state, goal)`: $h(state, goal) = ?$, that you define.  It must be admissible, and not constant for all states.

## Comparison

Apply all four algorithms (`iterativeDeepeningSearch` plus `aStarSearch` with the three heuristic
functions) to three eight-tile puzzle problems with start state

$$
\begin{array}{ccc}
1 & 2 & 3\\
4 & 0 & 5\\
6 & 7 & 8
\end{array}
$$

and these three goal states.

$$
\begin{array}{ccccccccccc}
1 & 2 & 3  & ~~~~ & 1 & 2 & 3  &  ~~~~ & 1 & 0 &  3\\
4 & 0 & 5  & & 4 & 5 & 8  & & 4 & 5 & 8\\
6 & 7 & 8 &  & 6 & 0 & 7  & & 2 & 6 & 7
\end{array}
$$

Print a well-formatted table like the following.  Try to match this
format. 

           [1, 2, 3, 4, 0, 5, 6, 7, 8]    [1, 2, 3, 4, 5, 8, 6, 0, 7]    [1, 0, 3, 4, 5, 8, 2, 6, 7] 
    Algorithm    Depth  Nodes  EBF              Depth  Nodes  EBF              Depth  Nodes  EBF          
         IDS       0      0  0.000                3     43  3.086               11 225850  2.954         
        A*h1       0      0  0.000                3    116  4.488               11 643246  3.263         
        A*h2       0      0  0.000                3     51  3.297               11 100046  2.733         

Of course you will have one more line for `h3`.

Download [A3grader.tar](http://www.cs.colostate.edu/~anderson/cs440/notebooks/A3grader.tar) and extract A3grader.py from it.

# IDS

In [ ]:
#%%writefile aStarSearch.py
# Recursive Best First Search (Figure 3.26, Russell and Norvig)
#  Recursive Iterative Deepening form of A*, where depth is replaced by f(n)

class Node:
    def __init__(self, state, f=0, g=0 ,h=0):
        self.state = state
        self.f = f
        self.g = g
        self.h = h
    def __repr__(self):
        return "Node(" + repr(self.state) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"

def aStarSearch(startState, actionsF, takeActionF, goalTestF, hF):
    global depth
    ebfValue=0
    h = hF(startState)
    startNode = Node(state=startState, f=0+h, g=0, h=h)
    a= aStarSearchHelper(startNode, actionsF, takeActionF, goalTestF, hF, float('inf'))
    depth=len(a)
    print depth
    print nNodes
    ebfValue= ebf(nNodes,depth)
    return a,ebfValue

def aStarSearchHelper(parentNode, actionsF, takeActionF, goalTestF, hF, fmax):
    global nNodes
    if goalTestF(parentNode.state):
        return ([parentNode.state], parentNode.g)
    ## Construct list of children nodes with f, g, and h values
    actions = actionsF(parentNode.state)
    if not actions:
        return ("failure", float('inf'))
    children = []
    for action in actions:
        (childState,stepCost) = takeActionF(parentNode.state, action)
        h = hF(childState)
        g = parentNode.g + stepCost
        f = max(h+g, parentNode.f)
        childNode = Node(state=childState, f=f, g=g, h=h)
        children.append(childNode)
        nNodes+=1

    while True:
        # find best child
        children.sort(key = lambda n: n.f) # sort by f value
        bestChild = children[0]
        if bestChild.f > fmax:
            return ("failure",bestChild.f)
        # next lowest f value
        alternativef = children[1].f if len(children) > 1 else float('inf')
        # expand best child, reassign its f value to be returned value
        result,bestChild.f = aStarSearchHelper(bestChild, actionsF, takeActionF, goalTestF,
                                            hF, min(fmax,alternativef))
        if result is not "failure":               #        g
            result.insert(0,parentNode.state)     #       / 
            return (result, bestChild.f)  
            
                                                  #      d
                                                  #     / \ 


In [ ]:
nNodes=0
depth=0

aStarSearch(start,actionsF,takeActionF,goalTestF,h1)


In [ ]:
def ebf(nodes, depth, precision=0.001):
    result=0
    d=depth
    b=0
    while (nodes-result) > precision:
        result=(1-b**(d+1))/(1-b)
        b+=precision
        
    return b
ebf(200000, 50)


In [13]:
def iterativeDeepeningSearch(startState, goalState, actionsF, takeActionF, maxDepth):
    path= 'cutoff'
    p=[]
    resultFound='false'
    for x in range(maxDepth+1):
        p= depthLimitedSearch(startState, goalState, actionsF, takeActionF, x)
        
        if p!='cutoff':
            return p
        
    if p=='cutoff':
        return 'cutoff'
    if p=='failure':
        return 'failure'
                


        

In [29]:
iterativeDeepeningSearch('a', 'z', actionsF_simple, takeActionF_simple, 10)

['a', 'c', 'h', 'i', 'k', 'z']

In [39]:
 iterativeDeepeningSearch([5, 2, 8, 0, 1, 4, 3, 7, 6], 
                                 [0, 2, 3, 1, 4,  6, 7, 5, 8],
                                 actionsF_8p, takeActionF_8p, 10)

unexpanded [Node([5, 2, 8, 0, 1, 4, 3, 7, 6], f=0, g=0, h=0)]
expanded {}
unexpanded [Node([5, 2, 8, 0, 1, 4, 3, 7, 6], f=0, g=0, h=0)]
expanded {}
unexpanded [Node([5, 2, 8, 1, 0, 4, 3, 7, 6], f=1, g=1, h=0), Node([0, 2, 8, 5, 1, 4, 3, 7, 6], f=1, g=1, h=0), Node([5, 2, 8, 3, 1, 4, 0, 7, 6], f=1, g=1, h=0)]
expanded {(5, 2, 8, 0, 1, 4, 3, 7, 6): Node([5, 2, 8, 0, 1, 4, 3, 7, 6], f=0, g=0, h=0)}
unexpanded [Node([0, 2, 8, 5, 1, 4, 3, 7, 6], f=1, g=1, h=0), Node([5, 2, 8, 3, 1, 4, 0, 7, 6], f=1, g=1, h=0), Node([5, 2, 8, 1, 4, 0, 3, 7, 6], f=2, g=2, h=0), Node([5, 0, 8, 1, 2, 4, 3, 7, 6], f=2, g=2, h=0), Node([5, 2, 8, 1, 7, 4, 3, 0, 6], f=2, g=2, h=0)]
expanded {(5, 2, 8, 0, 1, 4, 3, 7, 6): Node([5, 2, 8, 0, 1, 4, 3, 7, 6], f=0, g=0, h=0), (5, 2, 8, 1, 0, 4, 3, 7, 6): Node([5, 2, 8, 1, 0, 4, 3, 7, 6], f=1, g=1, h=0)}
unexpanded [Node([5, 2, 8, 3, 1, 4, 0, 7, 6], f=1, g=1, h=0), Node([5, 2, 8, 1, 4, 0, 3, 7, 6], f=2, g=2, h=0), Node([5, 0, 8, 1, 2, 4, 3, 7, 6], f=2, g=2, h=0), Node([5, 

unexpanded [Node([5, 4, 2, 1, 8, 0, 3, 7, 6], f=6, g=6, h=0), Node([5, 4, 2, 1, 7, 8, 3, 0, 6], f=6, g=6, h=0), Node([5, 2, 8, 0, 4, 6, 1, 3, 7], f=6, g=6, h=0), Node([5, 2, 8, 0, 1, 6, 3, 4, 7], f=6, g=6, h=0), Node([5, 2, 8, 1, 6, 0, 3, 4, 7], f=6, g=6, h=0), Node([5, 0, 8, 1, 2, 6, 3, 4, 7], f=6, g=6, h=0), Node([1, 5, 8, 2, 4, 0, 3, 7, 6], f=6, g=6, h=0), Node([1, 0, 8, 2, 5, 4, 3, 7, 6], f=6, g=6, h=0), Node([1, 5, 8, 2, 7, 4, 3, 0, 6], f=6, g=6, h=0), Node([1, 5, 8, 3, 2, 4, 7, 0, 6], f=6, g=6, h=0), Node([5, 8, 4, 0, 1, 2, 3, 7, 6], f=6, g=6, h=0), Node([5, 0, 4, 1, 8, 2, 3, 7, 6], f=6, g=6, h=0), Node([5, 8, 4, 1, 7, 2, 3, 0, 6], f=6, g=6, h=0), Node([5, 8, 4, 1, 2, 6, 3, 0, 7], f=6, g=6, h=0), Node([5, 2, 8, 7, 4, 0, 1, 3, 6], f=6, g=6, h=0), Node([5, 0, 8, 7, 2, 4, 1, 3, 6], f=6, g=6, h=0), Node([5, 2, 8, 7, 3, 4, 1, 0, 6], f=6, g=6, h=0), Node([2, 0, 8, 5, 7, 4, 1, 3, 6], f=6, g=6, h=0), Node([5, 2, 8, 0, 1, 7, 3, 6, 4], f=6, g=6, h=0), Node([5, 0, 8, 1, 2, 7, 3, 6, 4], f=6,

expanded {(0, 1, 8, 2, 5, 4, 3, 7, 6): Node([0, 1, 8, 2, 5, 4, 3, 7, 6], f=5, g=5, h=0), (5, 2, 8, 0, 3, 4, 7, 1, 6): Node([5, 2, 8, 0, 3, 4, 7, 1, 6], f=4, g=4, h=0), (5, 2, 8, 1, 0, 4, 3, 7, 6): Node([5, 2, 8, 1, 0, 4, 3, 7, 6], f=1, g=1, h=0), (2, 1, 0, 5, 4, 8, 3, 7, 6): Node([2, 1, 0, 5, 4, 8, 3, 7, 6], f=5, g=5, h=0), (5, 0, 2, 1, 4, 8, 3, 7, 6): Node([5, 0, 2, 1, 4, 8, 3, 7, 6], f=4, g=4, h=0), (5, 2, 0, 1, 4, 8, 3, 7, 6): Node([5, 2, 0, 1, 4, 8, 3, 7, 6], f=3, g=3, h=0), (5, 2, 8, 0, 3, 1, 7, 6, 4): Node([5, 2, 8, 0, 3, 1, 7, 6, 4], f=6, g=6, h=0), (5, 8, 4, 3, 2, 0, 7, 1, 6): Node([5, 8, 4, 3, 2, 0, 7, 1, 6], f=6, g=6, h=0), (2, 8, 4, 5, 1, 6, 3, 0, 7): Node([2, 8, 4, 5, 1, 6, 3, 0, 7], f=6, g=6, h=0), (5, 4, 2, 1, 7, 8, 3, 0, 6): Node([5, 4, 2, 1, 7, 8, 3, 0, 6], f=6, g=6, h=0), (5, 0, 8, 1, 2, 4, 3, 7, 6): Node([5, 0, 8, 1, 2, 4, 3, 7, 6], f=2, g=2, h=0), (5, 2, 8, 0, 1, 4, 3, 7, 6): Node([5, 2, 8, 0, 1, 4, 3, 7, 6], f=0, g=0, h=0), (2, 1, 8, 5, 4, 6, 3, 7, 0): Node([2, 1, 8

unexpanded [Node([2, 1, 8, 3, 5, 4, 7, 6, 0], f=7, g=7, h=0), Node([2, 1, 8, 3, 0, 4, 7, 5, 6], f=7, g=7, h=0), Node([0, 2, 1, 5, 4, 8, 3, 7, 6], f=7, g=7, h=0), Node([2, 4, 1, 5, 0, 8, 3, 7, 6], f=7, g=7, h=0), Node([2, 1, 8, 5, 4, 6, 0, 3, 7], f=7, g=7, h=0), Node([2, 1, 8, 5, 0, 6, 3, 4, 7], f=7, g=7, h=0), Node([2, 1, 8, 7, 0, 4, 5, 3, 6], f=7, g=7, h=0), Node([0, 1, 8, 2, 7, 4, 5, 3, 6], f=7, g=7, h=0), Node([2, 1, 8, 5, 0, 7, 3, 6, 4], f=7, g=7, h=0), Node([2, 1, 0, 5, 7, 8, 3, 6, 4], f=7, g=7, h=0), Node([0, 2, 8, 5, 3, 1, 7, 6, 4], f=7, g=7, h=0), Node([5, 2, 8, 7, 3, 1, 0, 6, 4], f=7, g=7, h=0), Node([0, 5, 8, 3, 2, 1, 7, 6, 4], f=7, g=7, h=0), Node([5, 8, 0, 3, 2, 1, 7, 6, 4], f=7, g=7, h=0), Node([5, 2, 8, 3, 6, 1, 0, 7, 4], f=7, g=7, h=0), Node([5, 2, 8, 3, 6, 1, 7, 4, 0], f=7, g=7, h=0), Node([0, 5, 2, 3, 1, 8, 7, 6, 4], f=7, g=7, h=0), Node([5, 1, 2, 3, 0, 8, 7, 6, 4], f=7, g=7, h=0), Node([2, 8, 0, 5, 3, 4, 7, 1, 6], f=7, g=7, h=0), Node([2, 3, 8, 5, 0, 4, 7, 1, 6], f=7,

unexpanded [Node([5, 4, 2, 3, 1, 8, 7, 0, 6], f=8, g=8, h=0), Node([5, 4, 2, 1, 8, 6, 3, 0, 7], f=8, g=8, h=0), Node([5, 4, 2, 0, 7, 8, 1, 3, 6], f=8, g=8, h=0), Node([5, 4, 2, 1, 7, 0, 3, 6, 8], f=8, g=8, h=0), Node([5, 2, 8, 4, 6, 0, 1, 3, 7], f=8, g=8, h=0), Node([5, 0, 8, 4, 2, 6, 1, 3, 7], f=8, g=8, h=0), Node([5, 2, 8, 4, 3, 6, 1, 0, 7], f=8, g=8, h=0), Node([2, 0, 8, 5, 4, 6, 1, 3, 7], f=8, g=8, h=0), Node([2, 0, 8, 5, 1, 6, 3, 4, 7], f=8, g=8, h=0), Node([5, 2, 8, 3, 1, 6, 4, 0, 7], f=8, g=8, h=0), Node([5, 0, 2, 1, 6, 8, 3, 4, 7], f=8, g=8, h=0), Node([1, 5, 8, 0, 2, 6, 3, 4, 7], f=8, g=8, h=0), Node([5, 8, 6, 1, 2, 0, 3, 4, 7], f=8, g=8, h=0), Node([1, 0, 5, 2, 4, 8, 3, 7, 6], f=8, g=8, h=0), Node([1, 5, 8, 2, 4, 6, 3, 0, 7], f=8, g=8, h=0), Node([1, 8, 4, 2, 5, 0, 3, 7, 6], f=8, g=8, h=0), Node([1, 5, 8, 0, 7, 4, 2, 3, 6], f=8, g=8, h=0), Node([1, 5, 8, 2, 7, 0, 3, 6, 4], f=8, g=8, h=0), Node([1, 5, 8, 3, 2, 0, 7, 6, 4], f=8, g=8, h=0), Node([1, 5, 8, 0, 3, 4, 7, 2, 6], f=8,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


[Node([2, 1, 8, 4, 0, 6, 5, 3, 7], f=9, g=9, h=0), Node([0, 1, 8, 2, 4, 6, 5, 3, 7], f=9, g=9, h=0), Node([0, 1, 8, 2, 5, 6, 3, 4, 7], f=9, g=9, h=0), Node([2, 1, 8, 3, 5, 6, 0, 4, 7], f=9, g=9, h=0), Node([2, 1, 0, 5, 6, 8, 3, 4, 7], f=9, g=9, h=0), Node([2, 1, 8, 5, 6, 7, 3, 4, 0], f=9, g=9, h=0), Node([2, 1, 0, 7, 4, 8, 5, 3, 6], f=9, g=9, h=0), Node([2, 1, 8, 7, 4, 6, 5, 3, 0], f=9, g=9, h=0), Node([0, 2, 8, 7, 1, 4, 5, 3, 6], f=9, g=9, h=0), Node([2, 8, 0, 7, 1, 4, 5, 3, 6], f=9, g=9, h=0), Node([2, 1, 8, 7, 3, 4, 5, 6, 0], f=9, g=9, h=0), Node([1, 8, 0, 2, 7, 4, 5, 3, 6], f=9, g=9, h=0), Node([1, 7, 8, 2, 0, 4, 5, 3, 6], f=9, g=9, h=0), Node([0, 1, 8, 2, 5, 7, 3, 6, 4], f=9, g=9, h=0), Node([2, 1, 8, 3, 5, 7, 0, 6, 4], f=9, g=9, h=0), Node([2, 1, 8, 5, 6, 7, 0, 3, 4], f=9, g=9, h=0), Node([0, 2, 1, 5, 7, 8, 3, 6, 4], f=9, g=9, h=0), Node([2, 7, 1, 5, 0, 8, 3, 6, 4], f=9, g=9, h=0), Node([2, 8, 0, 5, 3, 1, 7, 6, 4], f=9, g=9, h=0), Node([2, 3, 8, 5, 0, 1, 7, 6, 4], f=9, g=9, h=0),

expanded {(2, 1, 8, 5, 6, 7, 3, 0, 4): Node([2, 1, 8, 5, 6, 7, 3, 0, 4], f=8, g=8, h=0), (1, 8, 0, 2, 5, 4, 3, 7, 6): Node([1, 8, 0, 2, 5, 4, 3, 7, 6], f=7, g=7, h=0), (2, 1, 8, 7, 3, 4, 5, 6, 0): Node([2, 1, 8, 7, 3, 4, 5, 6, 0], f=9, g=9, h=0), (5, 0, 2, 1, 4, 8, 3, 7, 6): Node([5, 0, 2, 1, 4, 8, 3, 7, 6], f=4, g=4, h=0), (0, 2, 8, 5, 3, 4, 7, 1, 6): Node([0, 2, 8, 5, 3, 4, 7, 1, 6], f=5, g=5, h=0), (2, 8, 0, 5, 7, 4, 3, 6, 1): Node([2, 8, 0, 5, 7, 4, 3, 6, 1], f=9, g=9, h=0), (2, 8, 4, 5, 7, 1, 0, 3, 6): Node([2, 8, 4, 5, 7, 1, 0, 3, 6], f=7, g=7, h=0), (5, 8, 0, 4, 2, 6, 1, 3, 7): Node([5, 8, 0, 4, 2, 6, 1, 3, 7], f=9, g=9, h=0), (1, 5, 2, 3, 4, 8, 7, 6, 0): Node([1, 5, 2, 3, 4, 8, 7, 6, 0], f=9, g=9, h=0), (1, 2, 0, 4, 5, 8, 3, 7, 6): Node([1, 2, 0, 4, 5, 8, 3, 7, 6], f=9, g=9, h=0), (5, 2, 8, 3, 4, 0, 7, 1, 6): Node([5, 2, 8, 3, 4, 0, 7, 1, 6], f=4, g=4, h=0), (0, 1, 8, 3, 5, 4, 7, 2, 6): Node([0, 1, 8, 3, 5, 4, 7, 2, 6], f=9, g=9, h=0), (5, 2, 0, 4, 6, 8, 1, 3, 7): Node([5, 2, 0

unexpanded [Node([2, 3, 8, 5, 1, 4, 0, 7, 6], f=9, g=9, h=0), Node([2, 3, 8, 5, 1, 4, 7, 6, 0], f=9, g=9, h=0), Node([3, 5, 2, 4, 0, 8, 7, 1, 6], f=9, g=9, h=0), Node([3, 5, 2, 7, 4, 8, 0, 1, 6], f=9, g=9, h=0), Node([0, 4, 2, 5, 3, 8, 7, 1, 6], f=9, g=9, h=0), Node([5, 4, 2, 7, 3, 8, 0, 1, 6], f=9, g=9, h=0), Node([5, 4, 0, 3, 8, 2, 7, 1, 6], f=9, g=9, h=0), Node([5, 4, 2, 3, 8, 6, 7, 1, 0], f=9, g=9, h=0), Node([5, 2, 8, 4, 0, 6, 3, 7, 1], f=9, g=9, h=0), Node([0, 2, 8, 5, 4, 6, 3, 7, 1], f=9, g=9, h=0), Node([0, 2, 8, 5, 3, 6, 7, 4, 1], f=9, g=9, h=0), Node([5, 2, 8, 7, 3, 6, 0, 4, 1], f=9, g=9, h=0), Node([0, 5, 8, 3, 2, 6, 7, 4, 1], f=9, g=9, h=0), Node([5, 8, 0, 3, 2, 6, 7, 4, 1], f=9, g=9, h=0), Node([3, 5, 0, 2, 4, 8, 7, 1, 6], f=9, g=9, h=0), Node([3, 5, 8, 2, 4, 6, 7, 1, 0], f=9, g=9, h=0), Node([3, 8, 0, 2, 5, 4, 7, 1, 6], f=9, g=9, h=0), Node([3, 5, 8, 2, 1, 4, 0, 7, 6], f=9, g=9, h=0), Node([3, 5, 8, 2, 1, 4, 7, 6, 0], f=9, g=9, h=0), Node([3, 5, 8, 7, 2, 4, 1, 6, 0], f=9,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [38]:
def depthLimitedSearch(st , goalState, actionsF, takeActionF,depthLimit):
    startState=Node(state=st)
    expanded={}
    #nitialize unExpanded to be a list containing the startState node. 
    #Its h value is calculated using hF, its g value is 0, and its f value is g+h.
    startState.h=0#hF(startState)
    startState.g=0
    startState.f=startState.h+startState.g
    startState.parent=Node('None')
    unexpanded= [startState]
    solutionPath=[]
    existingChildren=[]
    depth=0
    needTuple=False
    end= True
    children=[]
    needTuple=False
    #global nNodes=0
    #If startState is the goalState, return the list containing just startState
    if goalTestF_simple(startState.state, goalState)==True:
        return startState.state
    else:
        
        while unexpanded:
            print 'unexpanded', unexpanded
            print 'expanded', expanded
            
            
            #Pop from the front of unExpanded to get the best (lowest f value) node to expand.
            stateNode= unexpanded.pop(0)  
            
                
            
            #Add the node to the expanded dictionary, indexed by its state.
            if isinstance(stateNode.state, list):
                expanded[tuple(stateNode.state)]=stateNode
            else:
                 expanded[stateNode.state]=stateNode
                    

            #get depth          
            searchParent=stateNode.state
            predecesor=True
            steps=0
            while predecesor==True:
                if searchParent in expanded.keys():
                    steps=steps+1
                    searchParent=expanded[searchParent].parent.state              
                else:
                    predecesor=False
            
            children=[]
            if steps < depthLimit:
                #Generate the children of state node.
                listActions=actionsF(stateNode.state)
                #Generates successor depending on the posible moves  
                for eachAction in listActions:
                    #create new child
                    stateChild,cost=takeActionF(stateNode.state,eachAction)
                    ch=Node(state=stateChild)
                    #Update the g, h, f values and set parent node.
                    ch.g=stateNode.g+cost
                    ch.h=0#hF(ch)
                    ch.f=ch.g+ch.h
                    ch.parent=stateNode
                    children.append(ch)
              
                #Remove from children any nodes that are already either in expanded or 
                #unExpanded, unless the node in children has a lower f value.
                unExistingChildren=[]      
                for checkChildren in children:
                    checkChildrenState=checkChildren.state
                    presentInExpanded=False
                    #hasLowerValueExpanded=False
                    presentInUnexpanded=False
                    #hasLowerValueUnexpanded=False
                    for stateExpanded in expanded.keys():
                        if expanded[stateExpanded].state==checkChildrenState:
                            presentInExpanded=True


                    for stateUnexpanded in unexpanded:
                        if stateUnexpanded.state==checkChildrenState:
                            presentInUnexpanded=True        

                    if presentInExpanded==False and presentInUnexpanded==False:
                        unExistingChildren.append(checkChildren)
                children=[]
                for unExistingChildrenNode in unExistingChildren:
                    children.append(unExistingChildrenNode)
                #Insert the modified children list into the unExpanded list and sort by f values.
                for ch in children:
                    unexpanded.append(ch)
            
            solutionPath=[]
            #If goalState is in children:            
            for ch in children:
                if goalTestF_simple(ch.state, goalState)==True:                 
                    #Build the solution path as a list starting with goalState.
                    solutionPath.append(ch.state)
                    #Use the parent stored with each node in the expanded dictionary to construct the path.
                    parentE=ch.parent.state                   
                    if isinstance(parentE, list):
                        parentE=tuple(parentE)
                        needTuple=True
                    while parentE in expanded.keys():                        
                        solutionPath.append(parentE)
                        parentE=expanded[parentE].parent.state
                        if isinstance(parentE, list):
                            parentE=tuple(parentE)  
                    #convert list 
                    if  needTuple==True:
                        newSolutionPath=[]
                        for x in solutionPath:
                            lst= list(x)
                            newSolutionPath.append(lst)               
                        solutionPath= newSolutionPath 
                    
                    return list(reversed(solutionPath))
    

        return 'cutoff'

            

       
            
            

In [36]:
def h1_8p(state, goal):
    return 0

In [ ]:
import copy
def actionsF_simple(state):
    return  copy.copy(succs.get(state, []))

In [ ]:
#dictionary of successors
successors = {'a': ['b', 'c'], 'b':['e', 'f', 'g'], 'b':['a'], 'c':['h'], 'h':['i'], 'i':['j', 'k', 'l'], 'k':['z']}

successors

In [ ]:
#return valid actions paired with the single step cost
def actionsF_simple(s):                              #       \ 
        try:                                      #        j
            ## step cost of each action is 1
            return [(succ,1) for succ in successors[s]]
        except KeyError:
            return []    
actionsF_simple('a')

In [ ]:
#return the pair containing the new state and the path cost so far from the start state to the new state 
def takeActionF_simple(s,a):
        return a
takeActionF_simple('a',('b', 1))

In [ ]:

def goalTestF_simple(s,goal):
    return s == goal


In [ ]:
def hF_simple(s):
    return 0

In [ ]:
class Node:
    def __init__(self, state,f=0, g=0 ,h=0):
        self.state = state
        self.f = f
        self.g = g
        self.h = h  
        self.parent=Node
    def __repr__(self):
        return "Node(" + repr(self.state) + ", f=" + repr(self.f) + \
               ", g=" + repr(self.g) + ", h=" + repr(self.h) + ")"

In [ ]:
def test():
    return aStarSearch('a', actionsF, takeActionF,
                     lambda s: goalTestF(s, 'z'),hF)
        

    
test()

# 8-Puzzle

In [31]:
def printPath_8p(startState):
    length= len(startState)
    dim=0
    for c in range(length):
        counter=c**2
        if counter==length: 
            dim=c              
    for i in range(dim):
        for j in range(dim):
             print(startState[i*dim+j]), 
        print ''


In [32]:
def findBlank_8p(startState):
    blankPosition=[]
    length= len(startState)
    dim= 0
    for c in range(length):
        counter=c**2
        if counter==length: 
            dim=c 
    if 0 in startState:
       
        for row in range(dim):          
             for column in range(dim): 
                    if startState[row*dim+column]==0:
                        blankPosition.append(row)
                        blankPosition.append(column)
                        
    return blankPosition



In [33]:
def actionsF_8p(startState):
   
    action=[]
    
    #gets puzzle demension
    dim=0
    length= len(startState)
    for c in range(length):
        counter=c**2
        if counter==length: 
            dim=c  
    
    blankPosition=findBlank_8p(startState)
    row=blankPosition[0]
    column=blankPosition[1]
    blankPosition=row*dim+column
   
    #check if there is blank position
    if blankPosition !=-1:
        action=['left', 'right', 'up', 'down']
      

        #check left border
        for row in range(dim):
                if blankPosition in [row*dim]:
                        action.remove('left')
                        
        #check right border
        for row in range(dim):
            if blankPosition in [(row*dim)+(dim-1)]:
                     action.remove('right')
        
        #check top border
        if blankPosition -dim <0:
            action.remove('up')
            
        #check bottom border
        if blankPosition +dim >=len(startState):
            action.remove("down")        
    
    actionCost=[]
    for ac in action:
        actionCost.append((ac,1))
    return actionCost

In [ ]:
startState=[1, 0, 3, 5, 4, 2, 6, 7, 8]
if isinstance(startState, list):
    print 'c'

#actionsF_8p(startState)

In [34]:
def takeActionF_8p(startState, act):

    newState=[]
    invalidLeft='false'
    invalidRight='false'
    invalidDown='false'
    invalidUp='false'
    #gets puzzle demension
    dim=0
    length= len(startState)
    for c in range(length):
        counter=c**2
        if counter==length: 
            dim=c  
    
    blankPosition=findBlank_8p(startState)
    row=blankPosition[0]
    column=blankPosition[1]
    blankPosition=row*dim+column
    
    
    #check left border
    for r in range(dim):
        if blankPosition in [r*dim]:
            invalidLeft='true'
                   

    #check right border
    for row in range(dim):
        if blankPosition in [(r*dim)+(dim-1)]:
            invalidRight='true'

    #check top border
    if blankPosition -dim <0:
         invalidUp='true'

    #check bottom border
    if blankPosition +dim >=len(startState):
        invalidDown='true'  
    
    action=act[0]
    pos=0
    for x in startState:
        newState.append(x)
    if action=='left' and invalidLeft=='false':
        pos=blankPosition
        pos=pos-1
        newState[blankPosition]=startState[pos]
        newState[pos]=0
    if action=='right'and invalidRight=='false':
        pos=blankPosition
        pos=pos+1
        newState[blankPosition]=startState[pos]
        newState[pos]=0
    if action=='up' and invalidUp=='false':
        pos=blankPosition
        pos=pos-dim
        newState[blankPosition]=startState[pos]
        newState[pos]=0
    if action=='down' and invalidDown=='false':
        pos=blankPosition
        pos=pos+dim      
        newState[blankPosition]=startState[pos]
        newState[pos]=0
      
    return (newState,act[1])


In [35]:

def goalTestF_8p(s,goal):
    return s == goal


In [ ]:
startState=[1, 0, 3, 5, 4, 2, 6, 7, 8]
takeActionF_8p(startState, ('left', 1))

In [ ]:
depth=0
nNodes=0
aStarSearch([1, 2, 3, 4, 5, 6, 7, 0, 8],actionsF_8p, takeActionF_8p,
                     lambda s: goalTestF_8p(s, [0, 2, 3, 1, 4,  6, 7, 5, 8]),
                     hF)

In [ ]:
aStarSearch('a',actionsF_simple, takeActionF_simple,
            lambda s: goalTestF_simple(s, 'z'),
            lambda s: h_simple(s, 'z'))

In [ ]:
# from A3mysolution import *

In [ ]:
%run -i A3grader.py